# Lab 4

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/giswqs/geog-414/blob/master/book/labs/lab_04.ipynb)

## Submission requirements

1. Upload a screenshot of your map for each question.
2. Provide a link to your notebook on Colab. See instructions [here](https://geog-414.gishub.org/book/labs/instructions.html).

## Datasets

The datasets being used in the lab are listed below:

- [TIGER: US Census Counties](https://developers.google.com/earth-engine/datasets/catalog/TIGER_2018_Counties)
- [Landsat-9](https://developers.google.com/earth-engine/datasets/catalog/LANDSAT_LC09_C02_T1_L2)
- [Sentinel-2](https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S2_SR)
- [NAIP](https://developers.google.com/earth-engine/datasets/catalog/USDA_NAIP_DOQQ)

## Question 1

Write a program to find out how many counties are named `Knox` in the US.

In [1]:
import geemap
import ee
from geemap.datasets import DATA

In [2]:
ee.Initialize()

In [3]:
fc= ee.FeatureCollection('TIGER/2018/Counties')
subset= fc.filter(ee.Filter.eq('NAME', 'Knox'))

In [4]:
subset

In [5]:
geemap.ee_to_df(subset)

ALAND      AWATER CBSAFP CLASSFP COUNTYFP  COUNTYNS CSAFP FUNCSTAT  \
0  1855569287     8837382  23660      H1      095  00424249              A   
1  1336511196    20758105  47180      H1      083  00450366              A   
2  1000523138     3743713  30940      H1      121  00516907              A   
3   945684684  2017116243             H1      013  00581292              A   
4  1305376626     7307094             H1      103  00758506              A   
5  2870856403    81009708             H1      107  00835875              A   
6  1361052752    10720134  34540      H1      083  01074054   198        A   
7  1316572232    45558452  28940      H1      093  01639761   314        A   
8  2203109026    12577260             H1      275  01383923              A   

   GEOID     INTPTLAT      INTPTLON LSAD METDIVFP  MTFCC  NAME     NAMELSAD  \
0  17095  +40.9309446  -090.2137921   06           G4020  Knox  Knox County   
1  18083  +38.6883910  -087.4203544   06           G4020  Knox  Knox County   
2  21121  +36.8874755  -083.8556297   06           G4020  Knox  Knox County   
3  23013  +44.0420446  -069.0385145   06           G4020  Knox  Knox County   
4  29103  +40.1368559  -092.1468345   06           G4020  Knox  Knox County   
5  31107  +42.6344045  -097.8913492   06           G4020  Knox  Knox County   
6  39083  +40.4036198  -082.4223929   06           G4020  Knox  Knox County   
7  47093  +35.9927265  -083.9377209   06           G4020  Knox  Knox County   
8  48275  +33.6118897  -099.7303563   06           G4020  Knox  Knox County   

  STATEFP  
0      17  
1      18  
2      21  
3      23  
4      29  
5      31  
6      39  
7      47  
8      48

![](https://i.imgur.com/3Jg9P6X.png)

## Question 2

Display Knox county of Tennesse with outline only (no fill color) on the map. (Hint: The `STATEFP` of Tennessee is `47`)

In [6]:
m= geemap.Map(center=[40, -100], zoom=4)
m.addLayer(subset, {}, 'Knox County')
m

Map(center=[40, -100], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(ch…

In [7]:
knox= subset.filter(ee.Filter.eq('STATEFP', '47'))

In [8]:
style= {'color': 'ff0000ff', 'width': 2, 'lineType': 'solid', 'fillColor': '00000000'}
m.addLayer(knox.style(**style), {}, 'Knox County, TN')
m.centerObject(knox, 10)

In [9]:
text = "Made by Zhanchao Yang"
m.add_text(text, fontsize=20, position='bottomright')

![](https://i.imgur.com/28Iaw9b.png)

## Question 3

Use [Landsat-9](https://developers.google.com/earth-engine/datasets/catalog/LANDSAT_LC09_C02_T1_L2) data to create a cloud-free imagery for Knox County, TN. Display the imagery on the map with a proper band combination.

In [27]:
collection= (ee.ImageCollection('LANDSAT/LC09/C02/T1_L2')
             .filterDate('2022-1-1', '2022-12-31')
             .filter(ee.Filter.lt('CLOUD_COVER', 5))
)
image= collection.median()
vis_params= {
    'bands': ['SR_B7', 'SR_B5', 'SR_B4'],
    'min': 0,
    'max': 65455,
}

subset= image.clip(knox)

m.addLayer(subset, vis_params, 'Landsat 8')
m

Map(bottom=103299.0, center=[35.934652585994556, -83.92868041992189], controls=(WidgetControl(options=['positi…

![](https://i.imgur.com/m72amN0.png)

## Question 4

Use [Sentinel-2](https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S2_SR) data to create a cloud-free imagery for Knox County, TN. Display the imagery on the map with a proper band combination.

In [28]:
collection=(ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')
            .filterDate('2022-1-1', '2022-12-31')
            .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 5))
)
image= collection.median()

vis_params= {
    'bands': ['B8', 'B4', 'B3'],
    'min': 0,
    'max': 2000,
}

subset= image.clip(knox)

m.addLayer(subset, vis_params, 'Sentinel-2')
m

Map(bottom=103299.0, center=[35.934652585994556, -83.92868041992189], controls=(WidgetControl(options=['positi…

![](https://i.imgur.com/vM1M8Gc.png)

## Question 5

Use [NAIP](https://developers.google.com/earth-engine/datasets/catalog/USDA_NAIP_DOQQ) imagery to create a cloud-free imagery for Knox County, TN. Display the imagery on the map with a proper band combination.

In [29]:
collection= (ee.ImageCollection("USDA/NAIP/DOQQ")
             .filterDate('2021-1-1', '2021-12-31')       
)

image= collection.median()

vis_params= {
    'bands': ['N', 'R', 'G'],
    'min': 0,
    'max': 255,
}

subset= image.clip(knox)

m.addLayer(subset, vis_params, 'NAIP')
m

Map(bottom=206257.0, center=[35.957443980673624, -84.02343750000001], controls=(WidgetControl(options=['positi…

![](https://i.imgur.com/iZSGqGS.png)